In [1]:
import openpyxl as oxl
import pandas as pd
import numpy as np
import geopandas as gpd

from thefuzz import process as fzproc
from thefuzz import fuzz

import pathlib as plb

In [2]:
WORK_DIR = plb.Path().resolve().parent
INPUT_DIR = WORK_DIR / "data_inputs"
OUTPUT_DIR = WORK_DIR / "data_outputs"
NOTEBOOK_DIR = WORK_DIR / "notebooks"
SCRIPTS_DIR = WORK_DIR / "scripts"
PSGC_DIR = WORK_DIR.parent.parent / "E- Administrative Boundaries"
BOUNDS_DIR = WORK_DIR.parent.parent / "E- Administrative Boundaries" / "phl_adm_psa_namria_20231106_shp"
AGRI_DIR = WORK_DIR.parent / "agri_vulnerability"

In [3]:
import sys
sys.path.append(str(WORK_DIR))

from scripts import parse_cph_excel as pcxl
from scripts import preprocess_geolocation as pgeo

In [4]:
fp_cph_2b = INPUT_DIR / "2020 Report 2B_Attachment_Population.xlsx"
assert fp_cph_2b.exists()

In [5]:
fp_psgc = PSGC_DIR / "PSGC-1Q-2023-Publication-Datafile.xlsx"
assert fp_psgc.exists()

In [6]:
fp_ab3 = BOUNDS_DIR / "phl_admbnda_adm3_psa_namria_20231106.shp"
assert fp_ab3.exists()

In [7]:
target_sheet = "T5"

kwargs = {
    "start_row": 9,
    "n_footers": 5,
}

In [8]:
workbook = oxl.load_workbook(fp_cph_2b)
sheet = workbook[target_sheet]

In [9]:
sheet.delete_cols(3, 11)

In [10]:
sheet_full = pcxl.remove_blank_rows(sheet, **kwargs)

Deleting row number: 1
Deleting row number: 71
Deleting row number: 1331
Deleting row number: 7211
Deleting row number: 16311
Deleting row number: 23241
Deleting row number: 32901
Deleting row number: 43261
Deleting row number: 48791
Deleting row number: 57261
Deleting row number: 67061
Deleting row number: 76651
Deleting row number: 87151
Deleting row number: 92471
Deleting row number: 99401
Deleting row number: 103251
Deleting row number: 107031
Deleting row number: 112561
Deleting row number: 121941
Deleting row number: 121941


In [11]:
col_names = pd.read_excel(
    fp_psgc,
    sheet_name="PSGC",
    nrows=2
).columns.values.tolist()

col_names

['10-digit PSGC',
 'Name',
 'Correspondence Code',
 'Geographic Level',
 'Old names',
 'City Class',
 'Income\nClassification',
 'Urban / Rural\n(based on 2020 CPH)',
 '2015 Population',
 'Unnamed: 9',
 '2020 Population',
 'Unnamed: 11',
 'Status']

In [12]:
df_psgc = pd.read_excel(
    fp_psgc,
    sheet_name="PSGC",
    nrows=43789,
    dtype={col: str for col in col_names[:-5]}
)

df_psgc.head()

10-digit PSGC                      Name Correspondence Code  \
0    0100000000  Region I (Ilocos Region)           010000000   
1    0102800000              Ilocos Norte           012800000   
2    0102801000                     Adams           012801000   
3    0102801001                     Adams           012801001   
4    0102802000                   Bacarra           012802000   

  Geographic Level Old names City Class Income\nClassification  \
0              Reg       NaN        NaN                    NaN   
1             Prov       NaN        NaN                    1st   
2              Mun       NaN        NaN                    5th   
3              Bgy       NaN        NaN                    NaN   
4              Mun       NaN        NaN                    3rd   

  Urban / Rural\n(based on 2020 CPH) 2015 Population Unnamed: 9  \
0                                NaN         5026128        NaN   
1                                NaN          593081        NaN   
2                                NaN            1792        NaN   
3                                  R            1792        NaN   
4                                NaN           32215        NaN   

  2020 Population Unnamed: 11 Status  
0         5301139         NaN    NaN  
1          609588         NaN    NaN  
2            2189         NaN    NaN  
3            2189         NaN   Pob.  
4           33496         NaN    NaN

In [13]:
cities = pcxl.get_column_from_sheet(sheet_full, 1, substr="CITY", **kwargs)
cities

['CITY OF MANILA',
 'CITY OF MANDALUYONG',
 'CITY OF MARIKINA',
 'CITY OF PASIG',
 'QUEZON CITY',
 'CITY OF SAN JUAN',
 'CITY OF CALOOCAN',
 'CITY OF MALABON',
 'CITY OF NAVOTAS',
 'CITY OF VALENZUELA',
 'CITY OF LAS PIÑAS',
 'CITY OF MAKATI',
 'CITY OF MUNTINLUPA',
 'CITY OF PARAÑAQUE',
 'PASAY CITY',
 'CITY OF TAGUIG',
 'CITY OF BAGUIO',
 'CITY OF TABUK (Capital)',
 'CITY OF BATAC',
 'CITY OF LAOAG (Capital)',
 'CITY OF CANDON',
 'CITY OF VIGAN (Capital)',
 'CITY OF SAN FERNANDO (Capital)',
 'CITY OF ALAMINOS',
 'CITY OF DAGUPAN',
 'CITY OF SAN CARLOS',
 'CITY OF URDANETA',
 'TUGUEGARAO CITY (Capital)',
 'CITY OF CAUAYAN',
 'CITY OF ILAGAN (Capital)',
 'CITY OF SANTIAGO',
 'CITY OF BALANGA (Capital)',
 'CITY OF MALOLOS (Capital)',
 'CITY OF MEYCAUAYAN',
 'CITY OF SAN JOSE DEL MONTE',
 'CITY OF CABANATUAN',
 'CITY OF GAPAN',
 'SCIENCE CITY OF MUÑOZ',
 'CITY OF PALAYAN (Capital)',
 'SAN JOSE CITY',
 'MABALACAT CITY',
 'CITY OF SAN FERNANDO (Capital)',
 'CITY OF ANGELES',
 'CITY OF TARL

In [14]:
hucs = pcxl.get_huc_names(df_psgc, choices=cities)
hucs

7538                        CITY OF ANGELES
8745                       CITY OF OLONGAPO
12365              CITY OF LUCENA (Capital)
14323     CITY OF PUERTO PRINCESA (Capital)
20500              CITY OF ILOILO (Capital)
21741             CITY OF BACOLOD (Capital)
24067                CITY OF CEBU (Capital)
24353              CITY OF LAPU-LAPU (OPON)
24429                       CITY OF MANDAUE
27706            CITY OF TACLOBAN (Capital)
31506                     CITY OF ZAMBOANGA
32791                        CITY OF ILIGAN
33833      CITY OF CAGAYAN DE ORO (Capital)
34559                         CITY OF DAVAO
36037    CITY OF GENERAL SANTOS (DADIANGAS)
36665                        CITY OF MANILA
37578                   CITY OF MANDALUYONG
37606                      CITY OF MARIKINA
37623                         CITY OF PASIG
37654                           QUEZON CITY
37797                      CITY OF SAN JUAN
37820                      CITY OF CALOOCAN
38009                       CITY

In [15]:
sheet_hucs = pcxl.change_indent_based_on_series(sheet_full, hucs, delta_indent=1, **kwargs)

In [16]:
sheet_final = pcxl.change_indent_based_on_series(sheet_hucs, pd.Series(["SOUTHERN LEYTE"]), delta_indent=-1, **kwargs)
sheet_final = pcxl.change_indent_based_on_series(sheet_final, pd.Series(["EASTERN SAMAR"]), delta_indent=1, **kwargs)
sheet_final = pcxl.change_indent_based_on_series(sheet_final, pd.Series(["BINMALEY"]), delta_indent=1, **kwargs)

In [17]:
sheet_classified = pcxl.insert_indent_status_column(sheet_final, **kwargs)

In [18]:
workers_by_industry_data = list(sheet_classified.values)
workers_by_industry_data = [list(row) for row in workers_by_industry_data]

workers_by_industry_data = workers_by_industry_data[8:-7]

for row in workers_by_industry_data:
    print(row)

['R', 'PHILIPPINES', None]
['', 'Both Sexes', 40701685]
['', 'Agriculture, Forestry and Fishing', 9055265]
['', 'Mining and Quarrying', 165161]
['', 'Manufacturing', 2926189]
['', 'Electricity, Gas, Steam and Air Conditioning Supply', 74603]
['', 'Water Supply; Sewerage, Waste Management and Remediation Activities', 44797]
['', 'Construction', 4296926]
['', 'Wholesale and Retail Trade; Repair of Motor Vehicles and Motorcycles', 6704458]
['', 'Transportation and Storage', 3715402]
['', 'Accommodation and Food Service Activities', 1580248]
['', 'Information and Communication', 316063]
['', 'Financial and Insurance Activities', 642790]
['', 'Real Estate Activities', 133598]
['', 'Professional, Scientific and Technical Activities', 235887]
['', 'Administrative and Support Service Activities', 2267798]
['', 'Public Administration and Defense; Compulsory Social Security', 2146476]
['', 'Education', 1454629]
['', 'Human Health and Social Work Activities', 769470]
['', 'Arts, Entertainment and

In [19]:
df_col_names = ["loc_marker", "geolocation", "n_workers"]

df_worker_by_industry = pd.DataFrame(
    workers_by_industry_data,
    columns=df_col_names
)

df_worker_by_industry.head()

loc_marker                        geolocation   n_workers
0          R                        PHILIPPINES         NaN
1                                    Both Sexes  40701685.0
2             Agriculture, Forestry and Fishing   9055265.0
3                          Mining and Quarrying    165161.0
4                                 Manufacturing   2926189.0

In [20]:
df_worker_by_industry = pgeo.remove_national(df_worker_by_industry)
df_worker_by_industry.head()

loc_marker                                        geolocation   n_workers
1                                                    Both Sexes  40701685.0
2                             Agriculture, Forestry and Fishing   9055265.0
3                                          Mining and Quarrying    165161.0
4                                                 Manufacturing   2926189.0
5             Electricity, Gas, Steam and Air Conditioning S...     74603.0

In [21]:
df_worker_by_industry = pgeo.assign_region(df_worker_by_industry)
df_worker_by_industry.head()

loc_marker                                        geolocation   n_workers  \
1                                                    Both Sexes  40701685.0   
2                             Agriculture, Forestry and Fishing   9055265.0   
3                                          Mining and Quarrying    165161.0   
4                                                 Manufacturing   2926189.0   
5             Electricity, Gas, Steam and Air Conditioning S...     74603.0   

  region  
1    NaN  
2    NaN  
3    NaN  
4    NaN  
5    NaN

In [22]:
df_worker_by_industry = df_worker_by_industry[~df_worker_by_industry["region"].isna()]
df_worker_by_industry.head()

loc_marker                                        geolocation  n_workers  \
71                                                    Both Sexes  5598690.0   
72                             Agriculture, Forestry and Fishing    20619.0   
73                                          Mining and Quarrying     2922.0   
74                                                 Manufacturing   397234.0   
75             Electricity, Gas, Steam and Air Conditioning S...     5914.0   

                           region  
71  NATIONAL CAPITAL REGION (NCR)  
72  NATIONAL CAPITAL REGION (NCR)  
73  NATIONAL CAPITAL REGION (NCR)  
74  NATIONAL CAPITAL REGION (NCR)  
75  NATIONAL CAPITAL REGION (NCR)

In [23]:
is_province = df_worker_by_industry["loc_marker"] == "P"
df_worker_by_industry.loc[is_province, "province"] = df_worker_by_industry.loc[is_province, "geolocation"]

for region in df_worker_by_industry["region"].unique():
    is_in_region = df_worker_by_industry["region"] == region
    df_worker_by_industry.loc[is_in_region, "province"] = df_worker_by_industry.loc[is_in_region, "province"].ffill()

df_worker_by_industry = df_worker_by_industry[~is_province]

C:\Users\HOWARD\AppData\Local\Temp\ipykernel_17904\496945393.py:6: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df_worker_by_industry.loc[is_in_region, "province"] = df_worker_by_industry.loc[is_in_region, "province"].ffill()


In [24]:
is_ncr = df_worker_by_industry["region"] == "NATIONAL CAPITAL REGION (NCR)"
is_ncr_city = (is_ncr) & (df_worker_by_industry["province"].str.isupper())

df_worker_by_industry = df_worker_by_industry[~is_ncr_city]
df_worker_by_industry.loc[is_ncr, "province"] = "National Capital Region (NCR)"

df_worker_by_industry.head()

loc_marker                                        geolocation  n_workers  \
71                                                    Both Sexes  5598690.0   
72                             Agriculture, Forestry and Fishing    20619.0   
73                                          Mining and Quarrying     2922.0   
74                                                 Manufacturing   397234.0   
75             Electricity, Gas, Steam and Air Conditioning S...     5914.0   

                           region                       province  
71  NATIONAL CAPITAL REGION (NCR)  National Capital Region (NCR)  
72  NATIONAL CAPITAL REGION (NCR)  National Capital Region (NCR)  
73  NATIONAL CAPITAL REGION (NCR)  National Capital Region (NCR)  
74  NATIONAL CAPITAL REGION (NCR)  National Capital Region (NCR)  
75  NATIONAL CAPITAL REGION (NCR)  National Capital Region (NCR)

In [25]:
df_worker_by_industry = pgeo.rename_interim_province(df_worker_by_industry)
df_worker_by_industry.tail()

loc_marker                                        geolocation  \
121933                            Arts, Entertainment and Recreation   
121934                                      Other Service Activities   
121935             Activities of Households as Employers; Undiffe...   
121936             Activities of Extra-Territorial Organizations ...   
121937                                                  Not Reported   

        n_workers                                             region  \
121933       11.0  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...   
121934      415.0  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...   
121935        5.0  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...   
121936        0.0  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...   
121937        0.0  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...   

                       province  
121933  SPECIAL GEOGRAPHIC AREA  
121934  SPECIAL GEOGRAPHIC AREA  
121935  SPECIAL GEOGRAPHIC AREA  
121936  SPECIAL GEOGRAPHIC AREA  
121937  SPECIAL GEOGRAPHIC AREA

In [26]:
df_worker_by_industry = df_worker_by_industry[~df_worker_by_industry["geolocation"].isna()]

In [27]:
df_worker_by_industry = pgeo.rename_provinces_with_independent_cities(df_worker_by_industry)
df_worker_by_industry.head()

loc_marker                                        geolocation  n_workers  \
71                                                    Both Sexes  5598690.0   
72                             Agriculture, Forestry and Fishing    20619.0   
73                                          Mining and Quarrying     2922.0   
74                                                 Manufacturing   397234.0   
75             Electricity, Gas, Steam and Air Conditioning S...     5914.0   

                           region                       province  
71  NATIONAL CAPITAL REGION (NCR)  National Capital Region (NCR)  
72  NATIONAL CAPITAL REGION (NCR)  National Capital Region (NCR)  
73  NATIONAL CAPITAL REGION (NCR)  National Capital Region (NCR)  
74  NATIONAL CAPITAL REGION (NCR)  National Capital Region (NCR)  
75  NATIONAL CAPITAL REGION (NCR)  National Capital Region (NCR)

In [28]:
df_worker_by_industry = df_worker_by_industry[~df_worker_by_industry["province"].isna()]
df_worker_by_industry.head()

loc_marker                                        geolocation  n_workers  \
71                                                    Both Sexes  5598690.0   
72                             Agriculture, Forestry and Fishing    20619.0   
73                                          Mining and Quarrying     2922.0   
74                                                 Manufacturing   397234.0   
75             Electricity, Gas, Steam and Air Conditioning S...     5914.0   

                           region                       province  
71  NATIONAL CAPITAL REGION (NCR)  National Capital Region (NCR)  
72  NATIONAL CAPITAL REGION (NCR)  National Capital Region (NCR)  
73  NATIONAL CAPITAL REGION (NCR)  National Capital Region (NCR)  
74  NATIONAL CAPITAL REGION (NCR)  National Capital Region (NCR)  
75  NATIONAL CAPITAL REGION (NCR)  National Capital Region (NCR)

In [29]:
is_municipality = df_worker_by_industry["loc_marker"] == "M"
df_worker_by_industry.loc[is_municipality, "municipality"] = df_worker_by_industry.loc[is_municipality, "geolocation"]

for region in df_worker_by_industry["province"].unique():
    is_in_region = df_worker_by_industry["province"] == region
    df_worker_by_industry.loc[is_in_region, "municipality"] = df_worker_by_industry.loc[is_in_region, "municipality"].ffill()

df_worker_by_industry = df_worker_by_industry[~is_municipality]

df_worker_by_industry.head()

loc_marker                                        geolocation  n_workers  \
71                                                    Both Sexes  5598690.0   
72                             Agriculture, Forestry and Fishing    20619.0   
73                                          Mining and Quarrying     2922.0   
74                                                 Manufacturing   397234.0   
75             Electricity, Gas, Steam and Air Conditioning S...     5914.0   

                           region                       province municipality  
71  NATIONAL CAPITAL REGION (NCR)  National Capital Region (NCR)          NaN  
72  NATIONAL CAPITAL REGION (NCR)  National Capital Region (NCR)          NaN  
73  NATIONAL CAPITAL REGION (NCR)  National Capital Region (NCR)          NaN  
74  NATIONAL CAPITAL REGION (NCR)  National Capital Region (NCR)          NaN  
75  NATIONAL CAPITAL REGION (NCR)  National Capital Region (NCR)          NaN

In [30]:
df_worker_by_industry = df_worker_by_industry[~df_worker_by_industry["municipality"].isna()]
df_worker_by_industry.head()

loc_marker                                        geolocation  n_workers  \
141                                                    Both Sexes   789242.0   
142                             Agriculture, Forestry and Fishing     1284.0   
143                                          Mining and Quarrying      305.0   
144                                                 Manufacturing    31275.0   
145             Electricity, Gas, Steam and Air Conditioning S...      954.0   

                            region                       province  \
141  NATIONAL CAPITAL REGION (NCR)  National Capital Region (NCR)   
142  NATIONAL CAPITAL REGION (NCR)  National Capital Region (NCR)   
143  NATIONAL CAPITAL REGION (NCR)  National Capital Region (NCR)   
144  NATIONAL CAPITAL REGION (NCR)  National Capital Region (NCR)   
145  NATIONAL CAPITAL REGION (NCR)  National Capital Region (NCR)   

       municipality  
141  CITY OF MANILA  
142  CITY OF MANILA  
143  CITY OF MANILA  
144  CITY OF MANILA  
145  CITY OF MANILA

In [31]:
df_worker_by_industry = pgeo.assign_ncr_districts(df_worker_by_industry, geoloc_col="municipality")
df_worker_by_industry.head()

loc_marker                                        geolocation  n_workers  \
141                                                    Both Sexes   789242.0   
142                             Agriculture, Forestry and Fishing     1284.0   
143                                          Mining and Quarrying      305.0   
144                                                 Manufacturing    31275.0   
145             Electricity, Gas, Steam and Air Conditioning S...      954.0   

                            region                            province  \
141  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA FIRST DISTRICT   
142  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA FIRST DISTRICT   
143  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA FIRST DISTRICT   
144  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA FIRST DISTRICT   
145  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA FIRST DISTRICT   

       municipality  
141  CITY OF MANILA  
142  CITY OF MANILA  
143  CITY OF MANILA  
144  CITY OF MANILA  
145  CITY OF MANILA

In [32]:
df_worker_by_industry = pgeo.rename_city_isabela(df_worker_by_industry, muni_col="municipality")
df_worker_by_industry[df_worker_by_industry["municipality"].str.contains("CITY OF ISABELA")]

loc_marker                                        geolocation  \
92401                                                    Both Sexes   
92402                             Agriculture, Forestry and Fishing   
92403                                          Mining and Quarrying   
92404                                                 Manufacturing   
92405             Electricity, Gas, Steam and Air Conditioning S...   
...          ...                                                ...   
92464                            Arts, Entertainment and Recreation   
92465                                      Other Service Activities   
92466             Activities of Households as Employers; Undiffe...   
92467             Activities of Extra-Territorial Organizations ...   
92468                                                  Not Reported   

       n_workers                           region  \
92401    40329.0  REGION IX (ZAMBOANGA PENINSULA)   
92402     8748.0  REGION IX (ZAMBOANGA PENINSULA)   
92403      164.0  REGION IX (ZAMBOANGA PENINSULA)   
92404      623.0  REGION IX (ZAMBOANGA PENINSULA)   
92405      177.0  REGION IX (ZAMBOANGA PENINSULA)   
...          ...                              ...   
92464        0.0  REGION IX (ZAMBOANGA PENINSULA)   
92465     1142.0  REGION IX (ZAMBOANGA PENINSULA)   
92466       70.0  REGION IX (ZAMBOANGA PENINSULA)   
92467        0.0  REGION IX (ZAMBOANGA PENINSULA)   
92468     2677.0  REGION IX (ZAMBOANGA PENINSULA)   

                               province     municipality  
92401  CITY OF ISABELA (NOT A PROVINCE)  CITY OF ISABELA  
92402  CITY OF ISABELA (NOT A PROVINCE)  CITY OF ISABELA  
92403  CITY OF ISABELA (NOT A PROVINCE)  CITY OF ISABELA  
92404  CITY OF ISABELA (NOT A PROVINCE)  CITY OF ISABELA  
92405  CITY OF ISABELA (NOT A PROVINCE)  CITY OF ISABELA  
...                                 ...              ...  
92464  CITY OF ISABELA (NOT A PROVINCE)  CITY OF ISABELA  
92465  CITY OF ISABELA (NOT A PROVINCE)  CITY OF ISABELA  
92466  CITY OF ISABELA (NOT A PROVINCE)  CITY OF ISABELA  
92467  CITY OF ISABELA (NOT A PROVINCE)  CITY OF ISABELA  
92468  CITY OF ISABELA (NOT A PROVINCE)  CITY OF ISABELA  

[68 rows x 6 columns]

In [33]:
is_sex = df_worker_by_industry["geolocation"].isin(["Both Sexes", "Male", "Female"])

df_worker_by_industry.loc[is_sex, "sex"] = df_worker_by_industry.loc[is_sex, "geolocation"]
df_worker_by_industry["sex"] = df_worker_by_industry["sex"].ffill()

df_worker_by_industry.loc[is_sex, "geolocation"] = "Total"

df_worker_by_industry.head()

loc_marker                                        geolocation  n_workers  \
141                                                         Total   789242.0   
142                             Agriculture, Forestry and Fishing     1284.0   
143                                          Mining and Quarrying      305.0   
144                                                 Manufacturing    31275.0   
145             Electricity, Gas, Steam and Air Conditioning S...      954.0   

                            region                            province  \
141  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA FIRST DISTRICT   
142  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA FIRST DISTRICT   
143  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA FIRST DISTRICT   
144  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA FIRST DISTRICT   
145  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA FIRST DISTRICT   

       municipality         sex  
141  CITY OF MANILA  Both Sexes  
142  CITY OF MANILA  Both Sexes  
143  CITY OF MANILA  Both Sexes  
144  CITY OF MANILA  Both Sexes  
145  CITY OF MANILA  Both Sexes

In [34]:
df_worker_by_industry = df_worker_by_industry[~(df_worker_by_industry["sex"] != "Both Sexes")].drop(columns="sex")
df_worker_by_industry.head()

loc_marker                                        geolocation  n_workers  \
141                                                         Total   789242.0   
142                             Agriculture, Forestry and Fishing     1284.0   
143                                          Mining and Quarrying      305.0   
144                                                 Manufacturing    31275.0   
145             Electricity, Gas, Steam and Air Conditioning S...      954.0   

                            region                            province  \
141  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA FIRST DISTRICT   
142  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA FIRST DISTRICT   
143  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA FIRST DISTRICT   
144  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA FIRST DISTRICT   
145  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA FIRST DISTRICT   

       municipality  
141  CITY OF MANILA  
142  CITY OF MANILA  
143  CITY OF MANILA  
144  CITY OF MANILA  
145  CITY OF MANILA

In [35]:
df_worker_by_industry.tail()

loc_marker                                        geolocation  \
121889                            Arts, Entertainment and Recreation   
121890                                      Other Service Activities   
121891             Activities of Households as Employers; Undiffe...   
121892             Activities of Extra-Territorial Organizations ...   
121893                                                  Not Reported   

        n_workers                                             region  \
121889       11.0  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...   
121890      472.0  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...   
121891        5.0  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...   
121892        0.0  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...   
121893        5.0  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...   

                       province       municipality  
121889  SPECIAL GEOGRAPHIC AREA  PIKIT CLUSTER III  
121890  SPECIAL GEOGRAPHIC AREA  PIKIT CLUSTER III  
121891  SPECIAL GEOGRAPHIC AREA  PIKIT CLUSTER III  
121892  SPECIAL GEOGRAPHIC AREA  PIKIT CLUSTER III  
121893  SPECIAL GEOGRAPHIC AREA  PIKIT CLUSTER III

In [36]:
# change lone error in industry type to intended industry type value
df_worker_by_industry.loc[df_worker_by_industry["geolocation"] == df_worker_by_industry["geolocation"].unique()[-1], "geolocation"] = df_worker_by_industry["geolocation"].unique()[-4]

In [37]:
df_pivot = pd.pivot_table(df_worker_by_industry, values=["n_workers"], index=["region", "province", "municipality"], columns=["geolocation"], aggfunc="sum", fill_value=0, dropna=True, sort=False).reset_index().rename_axis(columns=[None, None])
df_pivot.head()

region                             province  \
                                                                        
0  NATIONAL CAPITAL REGION (NCR)   METROPOLITAN MANILA FIRST DISTRICT   
1  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   
2  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   
3  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   
4  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   

          municipality  n_workers                                    \
                            Total Agriculture, Forestry and Fishing   
0       CITY OF MANILA   789242.0                            1284.0   
1  CITY OF MANDALUYONG   196094.0                             251.0   
2     CITY OF MARIKINA   178704.0                             575.0   
3        CITY OF PASIG   333152.0                             489.0   
4          QUEZON CITY  1219142.0                            3126.0   

                                      \
  Mining and Quarrying Manufacturing   
0                305.0       31275.0   
1                132.0        9728.0   
2                128.0       16183.0   
3                112.0       19805.0   
4                903.0       80684.0   

                                                       \
  Electricity, Gas, Steam and Air Conditioning Supply   
0                                              954.0    
1                                              535.0    
2                                              330.0    
3                                              314.0    
4                                             1372.0    

                                                                       \
  Water Supply; Sewerage, Waste Management and Remediation Activities   
0                                             1674.0                    
1                                              240.0                    
2                                              448.0                    
3                                              287.0                    
4                                             4707.0                    

                ...                                                    \
  Construction  ... Professional, Scientific and Technical Activities   
0      48994.0  ...                                            9544.0   
1      15992.0  ...                                            3623.0   
2      16907.0  ...                                            3277.0   
3      33358.0  ...                                            6509.0   
4     134808.0  ...                                           20352.0   

                                                 \
  Administrative and Support Service Activities   
0                                       87444.0   
1                                       35283.0   
2                                       30184.0   
3                                       70626.0   
4                                      186531.0   

                                                                           \
  Public Administration and Defense; Compulsory Social Security Education   
0                                            44447.0              20346.0   
1                                             8844.0               5175.0   
2                                             6196.0               6027.0   
3                                            12587.0               9026.0   
4                                            50849.0              33687.0   

                                                                              \
  Human Health and Social Work Activities Arts, Entertainment and Recreation   
0                                 26717.0                             5568.0   
1                                  6688.0                             1368.0   
2                                  6608.0                             1057.0   
3            

In [38]:
df_pivot.columns = df_pivot.columns.get_level_values(1)
df_pivot.columns = ["region", "province", "municipality"] + list(df_pivot.columns[3:])
df_pivot.head()

region                             province  \
0  NATIONAL CAPITAL REGION (NCR)   METROPOLITAN MANILA FIRST DISTRICT   
1  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   
2  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   
3  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   
4  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   

          municipality      Total  Agriculture, Forestry and Fishing  \
0       CITY OF MANILA   789242.0                             1284.0   
1  CITY OF MANDALUYONG   196094.0                              251.0   
2     CITY OF MARIKINA   178704.0                              575.0   
3        CITY OF PASIG   333152.0                              489.0   
4          QUEZON CITY  1219142.0                             3126.0   

   Mining and Quarrying  Manufacturing  \
0                 305.0        31275.0   
1                 132.0         9728.0   
2                 128.0        16183.0   
3                 112.0        19805.0   
4                 903.0        80684.0   

   Electricity, Gas, Steam and Air Conditioning Supply  \
0                                              954.0     
1                                              535.0     
2                                              330.0     
3                                              314.0     
4                                             1372.0     

   Water Supply; Sewerage, Waste Management and Remediation Activities  \
0                                             1674.0                     
1                                              240.0                     
2                                              448.0                     
3                                              287.0                     
4                                             4707.0                     

   Construction  ...  Professional, Scientific and Technical Activities  \
0       48994.0  ...                                             9544.0   
1       15992.0  ...                                             3623.0   
2       16907.0  ...                                             3277.0   
3       33358.0  ...                                             6509.0   
4      134808.0  ...                                            20352.0   

   Administrative and Support Service Activities  \
0                                        87444.0   
1                                        35283.0   
2                                        30184.0   
3                                        70626.0   
4                                       186531.0   

   Public Administration and Defense; Compulsory Social Security  Education  \
0                                            44447.0                20346.0   
1                                             8844.0                 5175.0   
2                                             6196.0                 6027.0   
3                                            12587.0                 9026.0   
4                                            50849.0                33687.0   

   Human Health and Social Work Activities  \
0                                  26717.0   
1                                   6688.0   
2                                   6608.0   
3                                   9470.0   
4                                  47303.0   

   Arts, Entertainment and Recreation  Other Service Activities  \
0                              5568.0                   50072.0   
1                              1368.0                   12899.0   
2                              1057.0                   11098.0   
3                              1059.0                   18586.0   
4                              7147.0                   90868.0   

   Activities of Households as Employers; Undifferentiated Goods-and Services_x0002_Producing Activities of Households for Own Use  \
0                                              243.0  

In [39]:
dict_rename_industry_cols = {
    'Total': 'n_workers',
    'Agriculture, Forestry and Fishing': 'n_agri',
    'Mining and Quarrying': 'n_mining',
    'Manufacturing': 'n_manuf',
    'Electricity, Gas, Steam and Air Conditioning Supply': 'n_power',
    'Water Supply; Sewerage, Waste Management and Remediation Activities': 'n_water',
    'Construction': 'n_build',
    'Wholesale and Retail Trade; Repair of Motor Vehicles and Motorcycles': 'n_trade',
    'Transportation and Storage': 'n_transpo',
    'Accommodation and Food Service Activities': 'n_accomm',
    'Information and Communication': 'n_ict',
    'Financial and Insurance Activities': 'n_finance',
    'Real Estate Activities': 'n_restate',
    'Professional, Scientific and Technical Activities': 'n_technical',
    'Administrative and Support Service Activities': 'n_support',
    'Public Administration and Defense; Compulsory Social Security': 'n_public',
    'Education': 'n_eduk',
    'Human Health and Social Work Activities': 'n_health',
    'Arts, Entertainment and Recreation': 'n_arts',
    'Other Service Activities': 'n_others',
    'Activities of Households as Employers; Undifferentiated Goods-and Services_x0002_Producing Activities of Households for Own Use': 'n_house',
    'Activities of Extra-Territorial Organizations and Bodies': 'n_extra',
    'Not Reported': 'n_blank'
}

df_pivot = df_pivot.rename(columns=dict_rename_industry_cols)
df_pivot.head()

region                             province  \
0  NATIONAL CAPITAL REGION (NCR)   METROPOLITAN MANILA FIRST DISTRICT   
1  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   
2  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   
3  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   
4  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   

          municipality  n_workers  n_agri  n_mining  n_manuf  n_power  \
0       CITY OF MANILA   789242.0  1284.0     305.0  31275.0    954.0   
1  CITY OF MANDALUYONG   196094.0   251.0     132.0   9728.0    535.0   
2     CITY OF MARIKINA   178704.0   575.0     128.0  16183.0    330.0   
3        CITY OF PASIG   333152.0   489.0     112.0  19805.0    314.0   
4          QUEZON CITY  1219142.0  3126.0     903.0  80684.0   1372.0   

   n_water   n_build  ...  n_technical  n_support  n_public   n_eduk  \
0   1674.0   48994.0  ...       9544.0    87444.0   44447.0  20346.0   
1    240.0   15992.0  ...       3623.0    35283.0    8844.0   5175.0   
2    448.0   16907.0  ...       3277.0    30184.0    6196.0   6027.0   
3    287.0   33358.0  ...       6509.0    70626.0   12587.0   9026.0   
4   4707.0  134808.0  ...      20352.0   186531.0   50849.0  33687.0   

   n_health  n_arts  n_others  n_house  n_extra  n_blank  
0   26717.0  5568.0   50072.0    243.0     91.0  10352.0  
1    6688.0  1368.0   12899.0    287.0     29.0   3732.0  
2    6608.0  1057.0   11098.0    994.0     34.0   1554.0  
3    9470.0  1059.0   18586.0   1609.0     11.0   2801.0  
4   47303.0  7147.0   90868.0   3394.0    262.0  48212.0  

[5 rows x 26 columns]

In [40]:
df_pivot["province"].unique()

array(['METROPOLITAN MANILA FIRST DISTRICT',
       'METROPOLITAN MANILA SECOND DISTRICT',
       'METROPOLITAN MANILA THIRD DISTRICT',
       'METROPOLITAN MANILA FOURTH DISTRICT', 'ABRA', 'BENGUET', 'IFUGAO',
       'KALINGA', 'MOUNTAIN PROVINCE', 'APAYAO', 'ILOCOS NORTE',
       'ILOCOS SUR', 'LA UNION', 'PANGASINAN', 'BATANES', 'CAGAYAN',
       'ISABELA', 'NUEVA VIZCAYA', 'QUIRINO', 'BATAAN', 'BULACAN',
       'NUEVA ECIJA', 'PAMPANGA', 'TARLAC', 'ZAMBALES', 'AURORA',
       'BATANGAS', 'CAVITE', 'LAGUNA', 'QUEZON', 'RIZAL', 'MARINDUQUE',
       'OCCIDENTAL MINDORO', 'ORIENTAL MINDORO', 'PALAWAN', 'ROMBLON',
       'ALBAY', 'CAMARINES NORTE', 'CAMARINES SUR', 'CATANDUANES',
       'MASBATE', 'SORSOGON', 'AKLAN', 'ANTIQUE', 'CAPIZ', 'ILOILO',
       'NEGROS OCCIDENTAL', 'GUIMARAS', 'BOHOL', 'CEBU',
       'NEGROS ORIENTAL', 'SIQUIJOR', 'EASTERN SAMAR', 'LEYTE',
       'NORTHERN SAMAR', 'SAMAR (WESTERN SAMAR)', 'SOUTHERN LEYTE',
       'BILIRAN', 'ZAMBOANGA DEL NORTE', 'ZAMBOANGA DE

In [41]:
df_agri = df_pivot[["region", "province", "municipality", "n_workers", "n_agri", "n_blank"]].copy(deep=True)
df_agri["pc_agri"] = (100 * df_agri["n_agri"] / (df_agri["n_workers"] - df_agri["n_blank"])).round(3)
df_agri.head()

region                             province  \
0  NATIONAL CAPITAL REGION (NCR)   METROPOLITAN MANILA FIRST DISTRICT   
1  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   
2  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   
3  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   
4  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   

          municipality  n_workers  n_agri  n_blank  pc_agri  
0       CITY OF MANILA   789242.0  1284.0  10352.0    0.165  
1  CITY OF MANDALUYONG   196094.0   251.0   3732.0    0.130  
2     CITY OF MARIKINA   178704.0   575.0   1554.0    0.325  
3        CITY OF PASIG   333152.0   489.0   2801.0    0.148  
4          QUEZON CITY  1219142.0  3126.0  48212.0    0.267

In [42]:
df_agri.sort_values("pc_agri", ascending=False).head()

region province  \
1610  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...     SULU   
1613  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...     SULU   
1617  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...     SULU   
1620  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...     SULU   
1616  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...     SULU   

                          municipality  n_workers   n_agri  n_blank  pc_agri  
1610  HADJI PANGLIMA TAHIL (MARUNGGAS)     4567.0   1533.0   3034.0  100.000  
1613                              PATA    14350.0   4975.0   9285.0   98.223  
1617                             TAPUL    11980.0   3179.0   8694.0   96.744  
1620                             LUGUS    16970.0   6031.0  10700.0   96.188  
1616                           TALIPAO    61737.0  19128.0  41664.0   95.292

In [43]:
gdf_ab3 = gpd.read_file(fp_ab3, engine="pyogrio")
gdf_ab3.head()

ADM3_EN ADM3_PCODE       ADM2_EN ADM2_PCODE  \
0          Adams  PH0102801  Ilocos Norte    PH01028   
1        Bacarra  PH0102802  Ilocos Norte    PH01028   
2          Badoc  PH0102803  Ilocos Norte    PH01028   
3         Bangui  PH0102804  Ilocos Norte    PH01028   
4  City of Batac  PH0102805  Ilocos Norte    PH01028   

                    ADM1_EN ADM1_PCODE            ADM0_EN ADM0_PCODE  \
0  Region I (Ilocos Region)       PH01  Philippines (the)         PH   
1  Region I (Ilocos Region)       PH01  Philippines (the)         PH   
2  Region I (Ilocos Region)       PH01  Philippines (the)         PH   
3  Region I (Ilocos Region)       PH01  Philippines (the)         PH   
4  Region I (Ilocos Region)       PH01  Philippines (the)         PH   

        date    validOn validTo ADM3_REF ADM3ALT1EN  Shape_Leng  Shape_Area  \
0 2022-11-09 2023-11-06     NaT     None       None    0.423604    0.009506   
1 2022-11-09 2023-11-06     NaT     None       None    0.309136    0.004725   
2 2022-11-09 2023-11-06     NaT     None       None    0.599295    0.006880   
3 2022-11-09 2023-11-06     NaT     None       None    0.483066    0.009843   
4 2022-11-09 2023-11-06     NaT     None       None    0.613500    0.013493   

    AREA_SQKM                                           geometry  
0  111.143026  POLYGON ((120.96915 18.51012, 120.95867 18.463...  
1   55.303195  POLYGON ((120.66821 18.28705, 120.66441 18.282...  
2   80.683970  POLYGON ((120.47814 17.97717, 120.47816 17.977...  
3  115.059041  POLYGON ((120.81318 18.53457, 120.81358 18.533...  
4  158.123132  POLYGON ((120.61242 18.10947, 120.612 18.10679...

In [44]:
is_special_area = gdf_ab3["ADM2_EN"] == "Special Geographic Area"

gdf_ab3.loc[is_special_area, "ADM3_EN"] = gdf_ab3.loc[is_special_area, "ADM3_EN"].str.replace("Special Geographic Area - ", "").str.replace(r"^(\w+) (\w+)$", "\\1 Cluster \\2", regex=True)

gdf_ab3[is_special_area]

ADM3_EN ADM3_PCODE                  ADM2_EN ADM2_PCODE  \
1634               Carmen  PH1909901  Special Geographic Area    PH19099   
1635              Kabacan  PH1909902  Special Geographic Area    PH19099   
1636   Midsayap Cluster I  PH1909903  Special Geographic Area    PH19099   
1637  Midsayap Cluster II  PH1909904  Special Geographic Area    PH19099   
1638           Pigkawayan  PH1909905  Special Geographic Area    PH19099   
1639      Pikit Cluster I  PH1909906  Special Geographic Area    PH19099   
1640     Pikit Cluster II  PH1909907  Special Geographic Area    PH19099   
1641    Pikit Cluster III  PH1909908  Special Geographic Area    PH19099   

                                                ADM1_EN ADM1_PCODE  \
1634  Bangsamoro Autonomous Region In Muslim Mindana...       PH19   
1635  Bangsamoro Autonomous Region In Muslim Mindana...       PH19   
1636  Bangsamoro Autonomous Region In Muslim Mindana...       PH19   
1637  Bangsamoro Autonomous Region In Muslim Mindana...       PH19   
1638  Bangsamoro Autonomous Region In Muslim Mindana...       PH19   
1639  Bangsamoro Autonomous Region In Muslim Mindana...       PH19   
1640  Bangsamoro Autonomous Region In Muslim Mindana...       PH19   
1641  Bangsamoro Autonomous Region In Muslim Mindana...       PH19   

                ADM0_EN ADM0_PCODE       date    validOn validTo ADM3_REF  \
1634  Philippines (the)         PH 2022-11-09 2023-11-06     NaT     None   
1635  Philippines (the)         PH 2022-11-09 2023-11-06     NaT     None   
1636  Philippines (the)         PH 2022-11-09 2023-11-06     NaT     None   
1637  Philippines (the)         PH 2022-11-09 2023-11-06     NaT     None   
1638  Philippines (the)         PH 2022-11-09 2023-11-06     NaT     None   
1639  Philippines (the)         PH 2022-11-09 2023-11-06     NaT     None   
1640  Philippines (the)         PH 2022-11-09 2023-11-06     NaT     None   
1641  Philippines (the)         PH 2022-11-09 2023-11-06     NaT     None   

     ADM3ALT1EN  Shape_Leng  Shape_Area   AREA_SQKM  \
1634       None    0.795495    0.007712   94.198423   
1635       None    0.715854    0.008644  105.576713   
1636       None    0.463561    0.003787   46.260412   
1637       None    0.299565    0.004123   50.379445   
1638       None    0.427476    0.003976   48.560572   
1639       None    0.825309    0.004857   59.337843   
1640       None    0.600366    0.006629   80.999972   
1641       None    0.569338    0.004707   57.516817   

                                               geometry  
1634  MULTIPOLYGON (((124.84027 7.27074, 124.84202 7...  
1635  MULTIPOLYGON (((124.8933 7.31157, 124.91048 7....  
1636  MULTIPOLYGON (((124.46757 7.22846, 124.46753 7...  
1637  POLYGON ((124.53774 7.08816, 124.52416 7.05555...  
1638  MULTIPOLYGON (((124.40575 7.36321, 124.41316 7...  
1639  MULTIPOLYGON (((124.70394 7.19775, 124.70387 7...  
1640  POLYGON ((124.71662 7.01955, 124.71764 7.01802...  
1641  POLYGON ((124.61461 7.08943, 124.62444 7.0903,...

In [45]:
is_maguindanao = gdf_ab3["ADM2_EN"].str.contains(r"^Maguindanao", regex=True)

gdf_ab3.loc[is_maguindanao, "ADM2_EN"] = gdf_ab3.loc[is_maguindanao, "ADM2_EN"].str.replace(r"^(Maguindanao).*", "Maguindanao", regex=True)
gdf_ab3[is_maguindanao].sample(5)

ADM3_EN ADM3_PCODE      ADM2_EN ADM2_PCODE  \
1630                          Pandag  PH1908833  Maguindanao    PH19088   
1602         Sultan Kudarat (Nuling)  PH1908712  Maguindanao    PH19087   
1616  Sultan Sa Barongis (Lambayong)  PH1908813  Maguindanao    PH19088   
1600                         Matanog  PH1908709  Maguindanao    PH19087   
1628          Datu Anggal Midtimbang  PH1908831  Maguindanao    PH19088   

                                                ADM1_EN ADM1_PCODE  \
1630  Bangsamoro Autonomous Region In Muslim Mindana...       PH19   
1602  Bangsamoro Autonomous Region In Muslim Mindana...       PH19   
1616  Bangsamoro Autonomous Region In Muslim Mindana...       PH19   
1600  Bangsamoro Autonomous Region In Muslim Mindana...       PH19   
1628  Bangsamoro Autonomous Region In Muslim Mindana...       PH19   

                ADM0_EN ADM0_PCODE       date    validOn validTo ADM3_REF  \
1630  Philippines (the)         PH 2022-11-09 2023-11-06     NaT     None   
1602  Philippines (the)         PH 2022-11-09 2023-11-06     NaT     None   
1616  Philippines (the)         PH 2022-11-09 2023-11-06     NaT     None   
1600  Philippines (the)         PH 2022-11-09 2023-11-06     NaT     None   
1628  Philippines (the)         PH 2022-11-09 2023-11-06     NaT     None   

     ADM3ALT1EN  Shape_Leng  Shape_Area   AREA_SQKM  \
1630       None    0.365204    0.003652   44.654776   
1602     Nuling    0.781897    0.015065  183.988677   
1616  Lambayong    0.594924    0.008771  107.197753   
1600       None    0.540805    0.009185  112.116920   
1628       None    0.560189    0.002732   33.382898   

                                               geometry  
1630  POLYGON ((124.86485 6.72878, 124.85611 6.72172...  
1602  MULTIPOLYGON (((124.39602 7.35539, 124.38426 7...  
1616  POLYGON ((124.64997 6.95522, 124.6515 6.95339,...  
1600  POLYGON ((124.27868 7.55795, 124.28523 7.5261,...  
1628  POLYGON ((124.42003 7.05966, 124.41709 7.05113...

In [46]:
region_choices = gdf_ab3["ADM1_EN"].unique()
df_agri["reg_match"] = df_agri["region"].apply(
    lambda x: fzproc.extractOne(
        x,
        region_choices
    )[0]
)

df_agri.head()

region                             province  \
0  NATIONAL CAPITAL REGION (NCR)   METROPOLITAN MANILA FIRST DISTRICT   
1  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   
2  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   
3  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   
4  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   

          municipality  n_workers  n_agri  n_blank  pc_agri  \
0       CITY OF MANILA   789242.0  1284.0  10352.0    0.165   
1  CITY OF MANDALUYONG   196094.0   251.0   3732.0    0.130   
2     CITY OF MARIKINA   178704.0   575.0   1554.0    0.325   
3        CITY OF PASIG   333152.0   489.0   2801.0    0.148   
4          QUEZON CITY  1219142.0  3126.0  48212.0    0.267   

                       reg_match  
0  National Capital Region (NCR)  
1  National Capital Region (NCR)  
2  National Capital Region (NCR)  
3  National Capital Region (NCR)  
4  National Capital Region (NCR)

In [47]:
for region in df_agri["reg_match"].unique():
    is_in_region_df = df_agri["reg_match"] == region
    is_in_region_gdf = gdf_ab3["ADM1_EN"] == region
    province_choices = gdf_ab3.loc[is_in_region_gdf, "ADM2_EN"].unique()

    df_agri.loc[is_in_region_df, "prov_match"] = df_agri.loc[is_in_region_df, "province"].apply(
        lambda x: fzproc.extractOne(
            x,
            province_choices
        )[0]
    )

df_agri.head()

region                             province  \
0  NATIONAL CAPITAL REGION (NCR)   METROPOLITAN MANILA FIRST DISTRICT   
1  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   
2  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   
3  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   
4  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   

          municipality  n_workers  n_agri  n_blank  pc_agri  \
0       CITY OF MANILA   789242.0  1284.0  10352.0    0.165   
1  CITY OF MANDALUYONG   196094.0   251.0   3732.0    0.130   
2     CITY OF MARIKINA   178704.0   575.0   1554.0    0.325   
3        CITY OF PASIG   333152.0   489.0   2801.0    0.148   
4          QUEZON CITY  1219142.0  3126.0  48212.0    0.267   

                       reg_match                           prov_match  
0  National Capital Region (NCR)   Metropolitan Manila First District  
1  National Capital Region (NCR)  Metropolitan Manila Second District  
2  National Capital Region (NCR)  Metropolitan Manila Second District  
3  National Capital Region (NCR)  Metropolitan Manila Second District  
4  National Capital Region (NCR)  Metropolitan Manila Second District

In [48]:
for province in df_agri["prov_match"].unique():
    is_in_province_df = df_agri["prov_match"] == province
    is_in_province_gdf = gdf_ab3["ADM2_EN"] == province
    municipality_choices = gdf_ab3.loc[is_in_province_gdf, "ADM3_EN"].unique()

    df_agri.loc[is_in_province_df, "muni_match"] = df_agri.loc[is_in_province_df, "municipality"].apply(
        lambda x: fzproc.extractOne(
            x,
            municipality_choices,
            scorer=fuzz.WRatio
        )[0]
    )

df_agri.head()

region                             province  \
0  NATIONAL CAPITAL REGION (NCR)   METROPOLITAN MANILA FIRST DISTRICT   
1  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   
2  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   
3  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   
4  NATIONAL CAPITAL REGION (NCR)  METROPOLITAN MANILA SECOND DISTRICT   

          municipality  n_workers  n_agri  n_blank  pc_agri  \
0       CITY OF MANILA   789242.0  1284.0  10352.0    0.165   
1  CITY OF MANDALUYONG   196094.0   251.0   3732.0    0.130   
2     CITY OF MARIKINA   178704.0   575.0   1554.0    0.325   
3        CITY OF PASIG   333152.0   489.0   2801.0    0.148   
4          QUEZON CITY  1219142.0  3126.0  48212.0    0.267   

                       reg_match                           prov_match  \
0  National Capital Region (NCR)   Metropolitan Manila First District   
1  National Capital Region (NCR)  Metropolitan Manila Second District   
2  National Capital Region (NCR)  Metropolitan Manila Second District   
3  National Capital Region (NCR)  Metropolitan Manila Second District   
4  National Capital Region (NCR)  Metropolitan Manila Second District   

            muni_match  
0       City of Manila  
1  City of Mandaluyong  
2     City of Marikina  
3        City of Pasig  
4          Quezon City

In [49]:
df_agri[df_agri.duplicated(subset=["prov_match", "muni_match"], keep=False)]

Empty DataFrame
Columns: [region, province, municipality, n_workers, n_agri, n_blank, pc_agri, reg_match, prov_match, muni_match]
Index: []

In [50]:
target_keyword = "CAGAYAN"
df_agri[df_agri["region"].str.contains(target_keyword) & df_agri.duplicated(subset=["prov_match", "muni_match"], keep=False)]

Empty DataFrame
Columns: [region, province, municipality, n_workers, n_agri, n_blank, pc_agri, reg_match, prov_match, muni_match]
Index: []

In [51]:
gdf_merged = gdf_ab3.merge(
    df_agri[["prov_match", "muni_match", "n_workers", "n_agri", "n_blank", "pc_agri"]],
    how="left",
    left_on=["ADM2_EN", "ADM3_EN"],
    right_on=["prov_match", "muni_match"],
    validate="one_to_one"
).drop(columns=["prov_match", "muni_match"])

gdf_merged.head()

ADM3_EN ADM3_PCODE       ADM2_EN ADM2_PCODE  \
0          Adams  PH0102801  Ilocos Norte    PH01028   
1        Bacarra  PH0102802  Ilocos Norte    PH01028   
2          Badoc  PH0102803  Ilocos Norte    PH01028   
3         Bangui  PH0102804  Ilocos Norte    PH01028   
4  City of Batac  PH0102805  Ilocos Norte    PH01028   

                    ADM1_EN ADM1_PCODE            ADM0_EN ADM0_PCODE  \
0  Region I (Ilocos Region)       PH01  Philippines (the)         PH   
1  Region I (Ilocos Region)       PH01  Philippines (the)         PH   
2  Region I (Ilocos Region)       PH01  Philippines (the)         PH   
3  Region I (Ilocos Region)       PH01  Philippines (the)         PH   
4  Region I (Ilocos Region)       PH01  Philippines (the)         PH   

        date    validOn  ... ADM3_REF ADM3ALT1EN Shape_Leng  Shape_Area  \
0 2022-11-09 2023-11-06  ...     None       None   0.423604    0.009506   
1 2022-11-09 2023-11-06  ...     None       None   0.309136    0.004725   
2 2022-11-09 2023-11-06  ...     None       None   0.599295    0.006880   
3 2022-11-09 2023-11-06  ...     None       None   0.483066    0.009843   
4 2022-11-09 2023-11-06  ...     None       None   0.613500    0.013493   

    AREA_SQKM                                           geometry n_workers  \
0  111.143026  POLYGON ((120.96915 18.51012, 120.95867 18.463...    1018.0   
1   55.303195  POLYGON ((120.66821 18.28705, 120.66441 18.282...   16502.0   
2   80.683970  POLYGON ((120.47814 17.97717, 120.47816 17.977...   15004.0   
3  115.059041  POLYGON ((120.81318 18.53457, 120.81358 18.533...    6094.0   
4  158.123132  POLYGON ((120.61242 18.10947, 120.612 18.10679...   27896.0   

   n_agri  n_blank  pc_agri  
0   576.0      3.0   56.749  
1  7754.0      5.0   47.002  
2  7354.0    129.0   49.439  
3  2324.0     10.0   38.199  
4  9649.0     73.0   34.680  

[5 rows x 21 columns]

In [52]:
fp_out = OUTPUT_DIR / "PH_PercentAgriWorkers_PSA-CPH_2020.shp"
gdf_merged.to_crs("EPSG: 32651").to_file(fp_out)

c:\Users\HOWARD\miniconda3\envs\ccims\Lib\site-packages\pyogrio\raw.py:709: RuntimeWarning: Field date create as date field, though DateTime requested.
  ogr_write(
c:\Users\HOWARD\miniconda3\envs\ccims\Lib\site-packages\pyogrio\raw.py:709: RuntimeWarning: Field validOn create as date field, though DateTime requested.
  ogr_write(
c:\Users\HOWARD\miniconda3\envs\ccims\Lib\site-packages\pyogrio\raw.py:709: RuntimeWarning: Field validTo create as date field, though DateTime requested.
  ogr_write(
